In [2]:
import os
import glob
import json

def get_fn_kps(image_name_one, fn_root_path):
    print("\t &&&&&&&&&&& find fn kps start &&&&&&&&&&&")
    if not os.path.exists(fn_root_path):
        print("*******" + fn_root_path + "  is not exists!*******\n")
    print("image_name_one: ", image_name_one)
    #     filenames = glob.glob(fn_root_path + "/*.json")
    fn_image_name_all = []
    fn_kps_all_one_image = []
    flag = False
    ##########
    filename = fn_root_path + "mid_mota_images\\" + image_name_one[7:].replace("/", "\\") + ".json"
    print("the json file finded by image_name_one", filename)
    if not os.path.exists(filename):
        print("the file " + filename + "  is not exists!")
        return -1, []
    with open(filename) as fn_file:
        fn_data = json.load(fn_file)
    fn_image_name_one = fn_data["image_name"]
    print("fn_image_name_one: ", fn_image_name_one)
    if image_name_one == fn_image_name_one:
        flag = True
        for fn_person_one in fn_data["FN_kps"]:
            fn_kps_all_one_image += fn_data["FN_kps"][fn_person_one]
    else:
        print("$$$$$ the image ", image_name_one, " didn't find in the fn json file!!!, check!!!")

    ##########
    #     for i in range(len(filenames)):
    #         with open(filenames[i]) as fn_file:
    #             fn_data=json.load(fn_file)
    #         fn_image_name_one=fn_data["image_name"]
    # #         print(fn_image_name_one)
    #         fn_image_name_all.append(fn_image_name_one)

    #         if image_name_one==fn_image_name_one:
    #             flag=True
    #             for fn_person_one in fn_data["FN_kps"]:
    #                 fn_kps_all_one_image+=fn_data["FN_kps"][fn_person_one]
    #         else:
    #             continue
    #     if flag==False:
    #         print("$$$$$ the image ",image_name_one," didn't find in the fn json file!!!, check!!!")
    print("\t &&&&&&&&&&& find fn kps end &&&&&&&&&&&\n")
    return fn_image_name_one, fn_kps_all_one_image


def gt_kps_counting(gt_root_path, fn_root_path,fn_root_path_pre):
    if not os.path.exists(gt_root_path):
        print("*******" + gt_root_path + "  is not exists!*******\n")
    if not os.path.exists(fn_root_path):
        print("*******" + fn_root_path + "  is not exists!*******\n")

    filenames = glob.glob(gt_root_path + "/*.json")
    gt_image_name_all = []
    miss_person_all = 0
    gt_person_all = 0
    miss_kps_for_miss_people_all = 0
    gt_kps_all = 0
    gt_img_all = 0
    flow_miss_people=0
    flow_miss_kps=0

    for i in range(len(filenames)):
        with open(filenames[i]) as gt_file:
            data = json.load(gt_file)
        gt_data = data["annolist"]
        for imgidx in range(len(gt_data)):
            gt_img_all += 1
            gt_image_name_one = gt_data[imgidx]["image"][0]["name"]
            print("\nthe " + str(imgidx) + " image, \t", "image name: ", gt_image_name_one)
            gt_image_name_all.append(gt_image_name_one)

            print("**person number in one image: ", len(gt_data[imgidx]["annorect"]), "\n")
            if len(gt_data[imgidx]["annorect"]) == 0:
                miss_person_in_one_image = 0
                miss_person_in_one_image_pre = 0
                print("##miss_person_in_one_image: ", miss_person_in_one_image)
                miss_person_all += miss_person_in_one_image
            else:
                # find fn kps by image name
                fn_image_name, fn_kps = get_fn_kps(gt_image_name_one, fn_root_path)
                fn_image_name_pre,fn_kps_pre=get_fn_kps(gt_image_name_one,fn_root_path_pre)
                miss_person_in_one_image = 0
                miss_person_in_one_image_pre = 0

                for personidx in range(len(gt_data[imgidx]["annorect"])):
                    gt_person_all += 1
                    if len(gt_data[imgidx]["annorect"][personidx]["annopoints"]) == 0:
                        num_kps_one_person = 0
                        miss_kps_in_one_person = 0
                        miss_kps_in_one_person_pre=0
                    else:
                        num_kps_one_person = len(gt_data[imgidx]["annorect"][personidx]["annopoints"][0]["point"])
                        gt_kps_all += num_kps_one_person
                        print("**kps number in the " + str(personidx) + " person: ", num_kps_one_person)

                        miss_kps_in_one_person = 0
                        miss_kps_in_one_person_pre=0
                        if len(gt_data[imgidx]["annorect"][personidx]["annopoints"][0]["point"]) == 0:
                            num_kps_one_person = 0
                            miss_kps_in_one_person_pre=0
                        else:
                            for keypoint in gt_data[imgidx]["annorect"][personidx]["annopoints"][0]["point"]:
                                kps_x = keypoint["x"][0]
                                kps_y = keypoint["y"][0]
                                kps_id = keypoint["id"][0]
                                kps_one = [kps_x, kps_y, kps_id]

                                if kps_one in fn_kps:
                                    miss_kps_in_one_person += 1
                                if kps_one in fn_kps_pre:
                                    miss_kps_in_one_person_pre+=1
                                        
                                        
                                    
                        print("##miss_kps_in_one_person: ", miss_kps_in_one_person)

                    if miss_kps_in_one_person - num_kps_one_person >= 0 and miss_kps_in_one_person > 0:
                        miss_person_in_one_image += 1
                        miss_kps_for_miss_people_all += miss_kps_in_one_person
                        if miss_kps_in_one_person_pre-num_kps_one_person>=0 and miss_kps_in_one_person>0:
                            miss_person_in_one_image_pre+=1
                            flow_miss_kps+=miss_kps_in_one_person_pre
                print("##miss_person_in_one_image: ", miss_person_in_one_image)
                miss_person_all += miss_person_in_one_image
                flow_miss_people+=miss_person_in_one_image_pre
    
    
    optical_flow_expect_people=miss_person_all-flow_miss_people
    optical_flow_expect_kps=miss_kps_for_miss_people_all-flow_miss_kps
    print("********************** result **********************")
    print("##miss_person_all: ", miss_person_all)
    print("##gt_person_all: ", gt_person_all)
    print("##miss_kps_for_miss_people_all: ", miss_kps_for_miss_people_all)
    print("##gt_kps_all: ", gt_kps_all)
    print("##gt_img_all: ", gt_img_all)
    print("##miss_people_in_current_frame_and_miss_in_preframe: ", flow_miss_people)
    print("##miss_kps_in_current_frame_and_miss_in_preframe: ", flow_miss_kps)
    print("##optical_flow_expect_people: ", optical_flow_expect_people)
    print("##optical_flow_expect_kps: ", optical_flow_expect_kps)

gt_root_path = "/var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/lib/datasets/data/PoseTrackV1.0_Annots_val_json/"
fn_root_path = "/var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota/"
fn_root_path_pre = "/var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota_sub/"
gt_kps_counting(gt_root_path, fn_root_path,fn_root_path_pre)


the 0 image, 	 image name:  images/bonn_mpii_test_5sec/05833_mpii/00000001.jpg
**person number in one image:  2 

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/bonn_mpii_test_5sec/05833_mpii/00000001.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota/mid_mota_images\bonn_mpii_test_5sec\05833_mpii\00000001.jpg.json
fn_image_name_one:  images/bonn_mpii_test_5sec/05833_mpii/00000001.jpg
	 &&&&&&&&&&& find fn kps end &&&&&&&&&&&

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/bonn_mpii_test_5sec/05833_mpii/00000001.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota_sub/mid_mota_images\bonn_mpii_test_5sec\05833_mpii\00000001.jpg.json
fn_

the file /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota_sub/mid_mota_images\bonn_mpii_test_5sec\05833_mpii\00000120.jpg.json  is not exists!
**kps number in the 0 person:  15
##miss_kps_in_one_person:  0
**kps number in the 1 person:  14
##miss_kps_in_one_person:  0
##miss_person_in_one_image:  0

the 120 image, 	 image name:  images/bonn_mpii_test_5sec/05833_mpii/00000121.jpg
**person number in one image:  0 

##miss_person_in_one_image:  0

the 0 image, 	 image name:  images/bonn_mpii_test_5sec/15301_mpii/00000001.jpg
**person number in one image:  10 

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/bonn_mpii_test_5sec/15301_mpii/00000001.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota/mi

**kps number in the 2 person:  11
##miss_kps_in_one_person:  2
**kps number in the 3 person:  3
##miss_kps_in_one_person:  3
**kps number in the 4 person:  14
##miss_kps_in_one_person:  1
**kps number in the 5 person:  14
##miss_kps_in_one_person:  4
**kps number in the 6 person:  9
##miss_kps_in_one_person:  1
**kps number in the 7 person:  11
##miss_kps_in_one_person:  3
**kps number in the 8 person:  15
##miss_kps_in_one_person:  1
##miss_person_in_one_image:  1

the 45 image, 	 image name:  images/bonn_mpii_test_5sec/15301_mpii/00000046.jpg
**person number in one image:  9 

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/bonn_mpii_test_5sec/15301_mpii/00000046.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota/mid_mota_images\bonn_mpii_test_5sec\15301_mpii\00000046.jpg.json
fn_image_name_one:  images/bonn_

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/bonn_mpii_test_5sec/15301_mpii/00000095.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota_sub/mid_mota_images\bonn_mpii_test_5sec\15301_mpii\00000095.jpg.json
fn_image_name_one:  images/bonn_mpii_test_5sec/15301_mpii/00000095.jpg
	 &&&&&&&&&&& find fn kps end &&&&&&&&&&&

**kps number in the 0 person:  4
##miss_kps_in_one_person:  1
**kps number in the 1 person:  12
##miss_kps_in_one_person:  9
**kps number in the 2 person:  15
##miss_kps_in_one_person:  0
**kps number in the 3 person:  15
##miss_kps_in_one_person:  2
**kps number in the 4 person:  13
##miss_kps_in_one_person:  0
**kps number in the 5 person:  15
##miss_kps_in_one_person:  2
**kps number in the 6 person:  11
##miss_kps_in_one_person:  1
**kps number in the 7 person:  7
##miss_kps_in_one_person:  

**kps number in the 5 person:  15
##miss_kps_in_one_person:  7
**kps number in the 6 person:  6
##miss_kps_in_one_person:  1
**kps number in the 7 person:  8
##miss_kps_in_one_person:  3
##miss_person_in_one_image:  1

the 55 image, 	 image name:  images/mpii_5sec/013293_mpii/00000056.jpg
**person number in one image:  8 

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/mpii_5sec/013293_mpii/00000056.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota/mid_mota_images\mpii_5sec\013293_mpii\00000056.jpg.json
fn_image_name_one:  images/mpii_5sec/013293_mpii/00000056.jpg
	 &&&&&&&&&&& find fn kps end &&&&&&&&&&&

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/mpii_5sec/013293_mpii/00000056.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_

...

the 82 image, 	 image name:  images/bonn_mpii_test_5sec/24621_mpii/00000083.jpg
**person number in one image:  0 

##miss_person_in_one_image:  0

the 83 image, 	 image name:  images/bonn_mpii_test_5sec/24621_mpii/00000084.jpg
**person number in one image:  0 

##miss_person_in_one_image:  0

the 84 image, 	 image name:  images/bonn_mpii_test_5sec/24621_mpii/00000085.jpg
**person number in one image:  0 

##miss_person_in_one_image:  0

the 85 image, 	 image name:  images/bonn_mpii_test_5sec/24621_mpii/00000086.jpg
**person number in one image:  5 

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/bonn_mpii_test_5sec/24621_mpii/00000086.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota/mid_mota_images\bonn_mpii_test_5sec\24621_mpii\00000086.jpg.json
fn_image_name_one:  images/bonn_mpii_test_5sec/24621_mpii/0000

fn_image_name_one:  images/bonn_mpii_test_5sec/14293_mpii/00000060.jpg
	 &&&&&&&&&&& find fn kps end &&&&&&&&&&&

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/bonn_mpii_test_5sec/14293_mpii/00000060.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota_sub/mid_mota_images\bonn_mpii_test_5sec\14293_mpii\00000060.jpg.json
fn_image_name_one:  images/bonn_mpii_test_5sec/14293_mpii/00000060.jpg
	 &&&&&&&&&&& find fn kps end &&&&&&&&&&&

**kps number in the 0 person:  15
##miss_kps_in_one_person:  2
**kps number in the 1 person:  13
##miss_kps_in_one_person:  0
**kps number in the 2 person:  15
##miss_kps_in_one_person:  2
**kps number in the 3 person:  15
##miss_kps_in_one_person:  0
##miss_person_in_one_image:  0

the 60 image, 	 image name:  images/bonn_mpii_test_5sec/14293_mpii/00000061.jpg
**person number in one

fn_image_name_one:  images/bonn_mpii_test_v2_5sec/00522_mpii/00000062.jpg
	 &&&&&&&&&&& find fn kps end &&&&&&&&&&&

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/bonn_mpii_test_v2_5sec/00522_mpii/00000062.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota_sub/mid_mota_images\bonn_mpii_test_v2_5sec\00522_mpii\00000062.jpg.json
fn_image_name_one:  images/bonn_mpii_test_v2_5sec/00522_mpii/00000062.jpg
	 &&&&&&&&&&& find fn kps end &&&&&&&&&&&

**kps number in the 0 person:  15
##miss_kps_in_one_person:  8
**kps number in the 1 person:  15
##miss_kps_in_one_person:  8
**kps number in the 2 person:  11
##miss_kps_in_one_person:  11
**kps number in the 3 person:  14
##miss_kps_in_one_person:  14
**kps number in the 4 person:  15
##miss_kps_in_one_person:  15
**kps number in the 5 person:  15
##miss_kps_in_one_pers

fn_image_name_one:  images/bonn_mpii_test_v2_5sec/00522_mpii/00000097.jpg
	 &&&&&&&&&&& find fn kps end &&&&&&&&&&&

	 &&&&&&&&&&& find fn kps start &&&&&&&&&&&
image_name_one:  images/bonn_mpii_test_v2_5sec/00522_mpii/00000097.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota_sub/mid_mota_images\bonn_mpii_test_v2_5sec\00522_mpii\00000097.jpg.json
fn_image_name_one:  images/bonn_mpii_test_v2_5sec/00522_mpii/00000097.jpg
	 &&&&&&&&&&& find fn kps end &&&&&&&&&&&

**kps number in the 0 person:  15
##miss_kps_in_one_person:  1
**kps number in the 1 person:  15
##miss_kps_in_one_person:  3
**kps number in the 2 person:  15
##miss_kps_in_one_person:  11
**kps number in the 3 person:  11
##miss_kps_in_one_person:  8
**kps number in the 4 person:  15
##miss_kps_in_one_person:  7
**kps number in the 5 person:  15
##miss_kps_in_one_person

image_name_one:  images/bonn_mpii_test_v2_5sec/00522_mpii/00000145.jpg
the json file finded by image_name_one /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota_sub/mid_mota_images\bonn_mpii_test_v2_5sec\00522_mpii\00000145.jpg.json
the file /var/storage/shared/pnrsy/t-jiwan/DetectAndTrack-wjb/tools/show_results/01_R101_best_hungarian-4GPU.yaml_nms=0.500000_score=_0.050000_drop_low_conf=0.950000/mid_mota_sub/mid_mota_images\bonn_mpii_test_v2_5sec\00522_mpii\00000145.jpg.json  is not exists!
**kps number in the 0 person:  15
##miss_kps_in_one_person:  0
**kps number in the 1 person:  15
##miss_kps_in_one_person:  0
**kps number in the 2 person:  15
##miss_kps_in_one_person:  0
**kps number in the 3 person:  9
##miss_kps_in_one_person:  0
**kps number in the 4 person:  15
##miss_kps_in_one_person:  0
**kps number in the 5 person:  13
##miss_kps_in_one_person:  0
**kps number

[[251, 273.5, 0], [361, 281.5, 1], [512, 225, 3], [397, 252.5, 4], [300, 247.5, 5], [636, 227.5, 8], [715, 236.5, 13], [745.1092529, 186.9822083, 14], [394, 173, 0], [523, 204, 2], [539, 184, 3], [430, 204, 4], [381, 164, 5], [664, 242, 6], [604, 232, 7], [618, 140, 9], [666, 185, 10], [710, 228, 11], [616.4887695, 153.2525482, 12]]
